# Working with Linux foundation Delta Lake tables
Use SQL on Athena Spark to create, analyze and manage Delta Lake tables.

## Create Delta table

In this section, we will create a database in the Glue Data Catalog. Using following SQL, we can create a database called deltalakedb.


In [ ]:
%%sql
CREATE DATABASE deltalakedb

Next, in the database deltalakedb, we will create a delta lake table noaa_delta pointing to a location in S3 where we will load the data.

**Note**: Replace the location 's3://\<your-S3-bucket\>/\<prefix\>/' to your S3 bucket and prefix:

In [ ]:
%%sql
CREATE TABLE deltalakedb.noaa_delta(
station string, 
  date string, 
  latitude string, 
  longitude string, 
  elevation string, 
  name string, 
  temp string, 
  temp_attributes string, 
  dewp string, 
  dewp_attributes string, 
  slp string, 
  slp_attributes string, 
  stp string, 
  stp_attributes string, 
  visib string, 
  visib_attributes string, 
  wdsp string, 
  wdsp_attributes string, 
  mxspd string, 
  gust string, 
  max string, 
  max_attributes string, 
  min string, 
  min_attributes string, 
  prcp string, 
  prcp_attributes string, 
  sndp string, 
  frshtt string)
USING delta
PARTITIONED BY (year string)
LOCATION 's3://<your-S3-bucket>/<prefix>/noaadelta/'

## Insert data into the table
We will use INSERT INTO statement to populate above table by reading data from sparkblogdb.noaa_pq table created in previous blog post.


In [ ]:
%%sql
INSERT INTO deltalakedb.noaa_delta select * from sparkblogdb.noaa_pq

## Querying the Delta Lake table
Now that the data is inserted in the delta lake table, we can start analyzing it. Let’s run a Spark SQL to find the minimum recorded temperature for the 'SEATTLE TACOMA AIRPORT, WA US' location:


In [ ]:
%%sql
select name, year, max(MAX) as minimum_temperature 
from deltalakedb.noaa_delta
where name = 'SEATTLE TACOMA AIRPORT, WA US' 
group by 1,2

## Updating  data in Delta lake table
Let’s change the station name 'SEATTLE TACOMA AIRPORT, WA US' to 'Sea–Tac'. We can run UPDATE statement on Athena Spark to update the records of noaa_delta table.


In [ ]:
%%sql
UPDATE deltalakedb.noaa_delta
SET name = 'Sea-Tac'
WHERE name = 'SEATTLE TACOMA AIRPORT, WA US'

We will run previous SELECT query to find the minimum recorded temperature for the 'Sea-Tac' location and the result should be same as above.

In [ ]:
%%sql
select name, year, max(MAX) as minimum_temperature 
from deltalakedb.noaa_delta
where name = 'Sea-Tac' 
group by 1,2

## Compacting data files
In Athena Spark, you can run OPTIMIZE on Delta Lake table that will compact the small files into larger files, so the queries are not burdened by the small file overhead. To perform the compaction operation, run following query:

In [ ]:
%%sql
OPTIMIZE deltalakedb.noaa_delta

## Remove files no longer referenced by a Delta lake table
You can remove files stored in S3 no longer referenced by a delta table and are older than the retention threshold by running the VACCUM command on the delta table using Athena Spark.

In [ ]:
%%sql
VACUUM deltalakedb.noaa_delta

## Drop table and database
Run following Spark SQL to remove the delta lake table created above


In [ ]:
%%sql
DROP TABLE deltalakedb.noaa_delta

Run following Spark SQL to remove the database deltalakedb.

In [ ]:
%%sql
DROP DATABASE deltalakedb

Running DROP on delta lake table and database deletes the metadata for these objects, but does not automatically delete the data files in Amazon S3. You can run the following python code in the notebook’s cell to delete the data from the S3 location.

In [ ]:
import boto3

s3 = boto3.resource('s3')
bucket = s3.Bucket('<your-S3-bucket>')
bucket.objects.filter(Prefix="<prefix>/noaadelta/").delete()

To learn more about the SQL statements that can be run on Delta lake table using Athena Spark, refer Delta lake documentation over [here](https://docs.delta.io/2.0.2/quick-start.html#).